# Clean Tweets Indonesia

In [22]:
import numpy as np
import pandas as pd
import nltk
nltk.download('stopwords')
nltk.download('punkt')
from nltk.corpus import stopwords
import re
import string
from nltk.tokenize import word_tokenize
#from nltk.stem.wordnet import WordNetLemmatizer
from Sastrawi.Stemmer.StemmerFactory import StemmerFactory
import swifter

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Miqdad\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Miqdad\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping tokenizers\punkt.zip.


In [28]:
#DATASET_COLUMNS = ["target", "ids", "date", "flag", "user", "text"]
DATASET_ENCODING = "ISO-8859-1"
#data = pd.read_csv('training.1600000.processed.noemoticon.csv', encoding =DATASET_ENCODING, names=DATASET_COLUMNS)
data = pd.read_csv('tweets_662k.csv', encoding =DATASET_ENCODING, dtype={'text': "string"})
#data.drop(data.iloc[:, 3:13], inplace = True, axis = 1) 
data['text']=data['text'].apply(str)
X = data.iloc[:,[2]]
#Y = data.iloc[:,0]
#Y[Y == 4] = 1

In [29]:
#data.head()
X['text'].head()

0                                               Yessss
1    Pelajaran berharga dari orang yang kurang cerm...
2                                  Can... I marry you?
3    She did, with me only one direction so she is ...
4               Yg dahsyat kalo pasangan Anies dan UAS
Name: text, dtype: object

In [30]:
# Text-preprocessing

# Missing Values
num_missing_desc = data.isnull().sum()[2]    # No. of values with msising descriptions
print('Number of missing values: ' + str(num_missing_desc))
data = data.dropna()

TAG_CLEANING_RE = "@\S+"
# Remove @tags
X['text'] = X['text'].map(lambda x: re.sub(TAG_CLEANING_RE, ' ', x))

# Smart lowercase
X['text'] = X['text'].map(lambda x: x.lower())

# Remove numbers
X['text'] = X['text'].map(lambda x: re.sub(r'\d+', ' ', x))

# Remove links
TEXT_CLEANING_RE = "https?:\S+|http?:\S|[^A-Za-z0-9]+"
X['text'] = X['text'].map(lambda x: re.sub(TEXT_CLEANING_RE, ' ', x))

# Remove Punctuation
X['text']  = X['text'].map(lambda x: x.translate(x.maketrans('', '', string.punctuation)))

# Remove white spaces
X['text'] = X['text'].map(lambda x: x.strip())

# Tokenize into words
X['text'] = X['text'].map(lambda x: word_tokenize(x))
 
# Remove non alphabetic tokens
X['text'] = X['text'].map(lambda x: [word for word in x if word.isalpha()])

# Filter out stop words
stop_words = set(stopwords.words('indonesian'))
X['text'] = X['text'].map(lambda x: [w for w in x if not w in stop_words])
    
# Word Lemmatization
#lem = WordNetLemmatizer()
#X['text'] = X['text'].map(lambda x: [lem.lemmatize(word,"v") for word in x])


Number of missing values: 0


In [31]:
# create stemmer
factory = StemmerFactory()
stemmer = factory.create_stemmer()

# stemmed
def stemmed_wrapper(term):
    return stemmer.stem(term)

term_dict = {}

for document in X['text']:
    for term in document:
        if term not in term_dict:
            term_dict[term] = ' '
            
print(len(term_dict))
print("------------------------")

for term in term_dict:
    term_dict[term] = stemmed_wrapper(term)
    print(term,":" ,term_dict[term])
    
print(term_dict)
print("------------------------")


# apply stemmed term to dataframe
def get_stemmed_term(document):
    return [term_dict[term] for term in document]

X['text'] = X['text'].swifter.apply(get_stemmed_term)
#print(TWEET_DATA['tweet_tokens_stemmed'])

# Turn lists back to string
X['text'] = X['text'].map(lambda x: ' '.join(x))

181323
------------------------
yessss : yessss
pelajaran : ajar
berharga : harga
orang : orang
cermat : cermat
tergesa : gesa
terkecoh : kecoh
berhadapan : hadap
judul : judul
berita : berita
anies : anies
baswedan : baswedan
thanks : thanks
sharingnya : sharingnya
bro : bro
can : can
i : i
marry : marry
you : you
she : she
did : did
with : with
me : me
only : only
one : one
direction : direction
so : so
is : is
used : used
and : and
love : love
them : them
yg : yg
dahsyat : dahsyat
kalo : kalo
pasangan : pasang
uas : uas
na : na
xx : xx
my : my
host : host
mum : mum
has : has
taste : taste
bandingin : bandingin
jokowi : jokowi
helo : helo
bangun : bangun
anjing : anjing
menggonggong : gonggong
jalan : jalan
gp : gp
rk : rk
nggak : nggak
layak : layak
hny : hny
titik : titik
malu : malu
bersaing : saing
levelnya : level
sdh : sdh
mendunia : dunia
bolak : bolak
jabar : jabar
jateng : jateng
jakarta : jakarta
pulau : pulau
jawa : jawa
aja : aja
gubernur : gubernur
dki : dki
tanda : tand

apbd : apbd
top : top
dg : dg
anggaran : anggar
lem : lem
aibon : aibon
jg : jg
merangkul : rangkul
kaum : kaum
hoby : hoby
demo : demo
ttp : ttp
pemenangnya : menang
oke : oke
ogah : ogah
ahh : ahh
wilayahnya : wilayah
allah : allah
tabaraqallah : tabaraqallah
milik : milik
dikucurkan : kucur
dgn : dgn
perintah : perintah
mendukung : dukung
pejuang : juang
korupsi : korupsi
pimpin : pimpin
jujur : jujur
bersih : bersih
hebat : hebat
mengalahkan : kalah
ahok : ahok
bener : bener
tanggung : tanggung
informasi : informasi
lengkap : lengkap
faktanya : fakta
menyesatkan : sesat
org : org
malas : malas
baca : baca
isi : isi
lgsg : lgsg
menyimpulkan : simpul
disukai : suka
logikanya : logika
terbalik : balik
lawan : lawan
politiknya : politik
kenap : kenap
bis : bis
abisnaya : abisnaya
km : km
kiko : kiko
enakkk : enakkk
ikan : ikan
manies : manies
imut : imut
lucu : lucu
seperi : per
qbisa : qbisa
nari : nari
jaipong : jaipong
mamamu : mama
menyuruh : suruh
menguras : uras
bak : bak
istiqom

jaksarasabuzzerrp : jaksarasabuzzerrp
deh : deh
guys : guys
masi : mas
ernest : ernest
nanya : nanya
gua : gua
pengennya : ken
mah : mah
jirlah : jir
waduk : waduk
pdhl : pdhl
mosting : mosting
ttg : ttg
sosok : sosok
pas : pas
terbukti : bukti
keliru : keliru
klarifikasi : klarifikasi
bansos : bansos
pelit : pelit
hitung : hitung
darurat : darurat
belagak : bagak
duit : duit
miskin : miskin
taunya : tau
uda : uda
setor : setor
gbp : gbp
diem : diem
kedengeran : kedengeran
kadrun : kadrun
culas : culas
nowoczesn : nowoczesn
czyli : czyli
bez : bez
ludzi : ludzi
lgbt : lgbt
jest : jest
pan : pan
spadkobierc : spadkobierc
hitlera : hitlera
on : on
by : by
z : z
pana : pana
dumny : dumny
przypominam : przypominam
w : w
auschwitz : auschwitz
zabijano : zabijano
nie : nie
sandiaga : sandiaga
sebenernya : sebenernya
gw : gw
pengen : ken
intelektual : intelektual
tandem : tandem
ex : ex
militer : militer
menkeu : menkeu
bossman : bossman
menhan : menhan
rg : rg
mendik : dik
fz : fz
menpolhuka

opo : opo
kuwi : kuwi
ketatkan : ketat
thd : thd
rizal : rizal
sri : sri
mulyani : mulyani
bergabung : gabung
pertumbuhan : tumbuh
sakyahene : sakyahene
enuj : enuj
ce : ce
za : za
od : od
kiedy : kiedy
ascicielk : ascicielk
miasta : miasta
terendah : rendah
jm : jm
prime : prime
news : news
these : these
hands : hands
belong : bong
museum : museum
foto : foto
profil : profil
status : status
quote : quote
sedih : sedih
galau : galau
gk : gk
kehidupan : hidup
akutu : akutu
louis : louis
sweater : sweater
paws : paws
waeyoo : waeyoo
pakar : pakar
netizen : netizen
bego : bego
melindungin : melindungin
termsuk : termsuk
wajah : wajah
cek : cek
faceshield : faceshield
gojes : gojes
manage : manage
kutho : kutho
sekelas : kelas
target : target
dilampaui : lampau
sepekan : pek
tes : tes
keterangan : terang
fotonya : foto
nyalain : nyalain
mantabb : mantabb
takpe : takpe
slow : slow
mood : mood
hshs : hshs
drpd : drpd
jemput : jemput
baswwuedan : baswwuedan
sweet : sweet
babiest : babiest
viv

sexy : sexy
wabah : wabah
virus : virus
nasib : nasib
kebanggaan : bangga
formulae : formulae
wagub : wagub
patria : patria
random : random
question : question
kah : kah
work : work
balai : balai
bike : bike
biketowork : biketowork
mmg : mmg
maennya : maennya
alus : alus
pasangkan : pasang
periode : periode
liganya : liga
federasi : federasi
sepakbola : sepakbola
pluit : pluit
pertandingan : tanding
juara : juara
liga : liga
kaji : kaji
pelonggaran : longgar
fh : fh
sengaja : sengaja
tugaskan : tugas
menggiring : giring
trik : trik
busuk : busuk
dibayarkan : bayar
upeti : upeti
fim : fim
tamu : tamu
spesial : spesial
event : event
tahunan : tahun
forum : forum
muda : muda
perkara : perkara
undang : undang
mengundang : undang
bicara : bicara
seminar : seminar
longgarkan : longgar
denger : denger
ohh : ohh
novelnya : novel
bpk : bpk
air : air
ngetawain : ngetawain
donk : donk
prioritas : prioritas
membangun : bangun
masjid : masjid
etalase : etalase
kesenian : seni
kebudayaan : budaya
fe

...

kakibumi : kakibumi
kwanku : kwanku
awkakwk : awkakwk
basick : basick
twitual : twitual
gamplong : gamplong
filmnyal : filmnyal
aligator : aligator
hsmindonesia : hsmindonesia
zavrelindonesia : zavrelindonesia
internalmilitanmatch : internalmilitanmatch
ucqcddq : ucqcddq
gzkxlzyxqc : gzkxlzyxqc
mentadbirkan : tadbir
tilawahmalaysia : tilawahmalaysia
diliriknya : lirik
kepluto : pluto
stayhomestaysafe : stayhomestaysafe
seji : seji
kenangannmu : kenangannmu
pokemaon : pokemaon
infusan : infus
geokinesis : geokinesis
sturmanya : sturmanya
tololabis : tololabis
juliter : juliter
ckuptau : ckuptau
fbio : fbio
lohhhcok : lohhhcok
ngeneiki : ngeneiki
jgngkan : jgngkan
smsta : smsta
ibak : ibak
berseka : seka
khilapan : khilapan
panggungan : panggung
otpimal : otpimal
didasarkn : didasarkn
siakul : siakul
eissa : eissa
murnikan : murni
kesyirikan : syirik
dikembangbiakan : dikembangbiakan
gantirezim : gantirezim
ahel : ahel
ditwlen : ditwlen
astronomical : astronomical
deloken : deloken
apikk

blahan : blahan
mrebutnya : mrebutnya
uniat : uniat
saruwa : saruwa
kujunjung : junjung
zheyenk : zheyenk
humaspolda : humaspolda
ukjg : ukjg
ibidtj : ibidtj
wmce : wmce
renung : renung
dipercayanya : percaya
sjhhhhhh : sjhhhhhh
merangkaikan : rangkai
yxk : yxk
dallas : dallas
mnghalalkan : mnghalalkan
dsanalah : dsanalah
adtd : adtd
qeznps : qeznps
syb : syb
lutvc : lutvc
wcj : wcj
dicurah : curah
repb : repb
zlog : zlog
gasskeun : gasskeun
memijakkan : pijak
qyqpy : qyqpy
kzmm : kzmm
ngess : ngess
fial : fial
hadza : hadza
hahahy : hahahy
mjlah : mjlah
pngagum : pngagum
terpertjaja : terpertjaja
bawaanny : bawaanny
mengingatkanya : mengingatkanya
leeknowpopo : leeknowpopo
qauniyah : qauniyah
borealis : boreal
australis : australis
jiwajiwa : jiwajiwa
alshad : alshad
jinora : jinora
tergoncang : tergoncang
dimusnahin : dimusnahin
snepgrem : snepgrem
perlengakapan : perlengakapan
perigee : perigee
tadbir : tadbir
bobrokann : bobrokann
pererpean : pererpean
bumdes : bumdes
rengganis : r

bodyshamming : bodyshamming
dihidupmu : hidup
solusiislam : solusiislam
oenez : oenez
bbahaya : bbahaya
bragama : bragama
gablag : gablag
sudahhhh : sudahhhh
scnd : scnd
betet : betet
kmtot : kmtot
pabosku : pabosku
judulin : judulin
sqoq : sqoq
litd : litd
guqao : guqao
lmee : lmee
pbqiod : pbqiod
wjbngrzxw : wjbngrzxw
fisabillillah : fisabillillah
pingit : pingit
ditamannya : tam
yskrmvofa : yskrmvofa
lekaspulih : lekaspulih
beasiswapertamina : beasiswapertamina
alame : alame
dedungo : dedungo
kabegjan : kabegjan
waanjayy : waanjayy
hwaahhhh : hwaahhhh
intermezzo : intermezzo
hlngkan : hlngkan
nolongny : nolongny
indonesialawancorona : indonesialawancorona
lawancoronamulaidarikita : lawancoronamulaidarikita
composterprojectmerahputih : composterprojectmerahputih
washilah : washilah
kgzidx : kgzidx
tergeletek : geletek
tekaknya : tekak
tinantang : tantang
pancasunda : pancasunda
kapethak : kapethak
rasenenge : rasenenge
indahnyaa : indahnyaa
pemagaran : pagar
rancanganmu : rancang
mus

hsauj : hsauj
elektro : elektro
akuntasi : akuntasi
cheribon : cheribon
lokomotifcc : lokomotifcc
kaskusjualbeli : kaskusjualbeli
trobos : trobos
hxx : hxx
yhylhv : yhylhv
rove : rove
bmkgmultisektoral : bmkgmultisektoral
bmkgbandung : bmkgbandung
skincarepreloved : skincarepreloved
mediakonsumenid : mediakonsumenid
kepoy : kepoy
mmwaaah : mmwaaah
bateray : bateray
lnuy : lnuy
twitterfamous : twitterfamous
umh : umh
terdrag : terdrag
bersocial : bersocial
vbjmpqazj : vbjmpqazj
lingukangan : lingukangan
kblvszoq : kblvszoq
rayaaa : rayaaa
schannel : schannel
hvztvwlttbw : hvztvwlttbw
sweetmunchies : sweetmunchies
koreandrama : koreandrama
koreanupdates : koreanupdates
jungilwoo : jungilwoo
kangjiyoung : kangjiyoung
uyi : uyi
fifarasol : fifarasol
qbonjk : qbonjk
jjxb : jjxb
ltsqagsvyms : ltsqagsvyms
bfc : bfc
gnux : gnux
mencederakan : cedera
personalitinya : personalitinya
attendance : attendance
dolaras : dolaras
kursdolar : kursdolar
bersodakoh : bersodakoh
mengabsen : absen
wallstre

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [32]:
X.head()

text
0                                             yessss
1  ajar harga orang cermat gesa kecoh hadap judul...
2                                    can i marry you
3  she did with me only one direction so she is u...
4                   yg dahsyat kalo pasang anies uas

In [33]:
X.to_csv("Clean_Tweets_Indonesia_fix.csv")